# DataFrame & Column
##### Objectives
1. Construct columns
1. Subset columns
1. Add or replace columns
1. Subset rows
1. Sort rows

##### Methods
- <a href="https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.sql.DataFrame.html" target="_blank">DataFrame</a>: `select`, `selectExpr`, `drop`, `withColumn`, `withColumnRenamed`, `filter`, `distinct`, `limit`, `sort`
- <a href="https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.sql.Column.html" target="_blank">Column</a>: `alias`, `isin`, `cast`, `isNotNull`, `desc`, operators

In [0]:
%run ./Includes/Classroom-Setup

Finished setting up utiltity methods...

Datasets mounted and student environment set up

Let's use the BedBricks events dataset.

In [0]:
eventsDF = spark.read.parquet(eventsPath)
display(eventsDF)

## Column Expressions

A <a href="https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.sql.Column.html" target="_blank">Column</a> is a logical construction that will be computed based on the data in a DataFrame using an expression

Construct a new Column based on existing columns in a DataFrame

In [0]:
from pyspark.sql.functions import col

eventsDF.device
eventsDF["device"]
col("device")

Out[6]: Column<'device'>

Scala supports an additional syntax for creating a new Column based on existing columns in a DataFrame

In [0]:
%scala
$"device"

### Column Operators and Methods
| Method | Description |
| --- | --- |
| \*, + , <, >= | Math and comparison operators |
| ==, != | Equality and inequality tests (Scala operators are `===` and `=!=`) |
| alias | Gives the column an alias |
| cast, astype | Casts the column to a different data type |
| isNull, isNotNull, isNan | Is null, is not null, is NaN |
| asc, desc | Returns a sort expression based on ascending/descending order of the column |

Create complex expressions with existing columns, operators, and methods.

In [0]:
col("ecommerce.purchase_revenue_in_usd") + col("ecommerce.total_item_quantity")
col("event_timestamp").desc()
(col("ecommerce.purchase_revenue_in_usd") * 100).cast("int")

Here's an example of using these column expressions in the context of a DataFrame

In [0]:
revDF = (eventsDF
         .filter(col("ecommerce.purchase_revenue_in_usd").isNotNull())
         .withColumn("purchase_revenue", (col("ecommerce.purchase_revenue_in_usd") * 100).cast("int"))
         .withColumn("avg_purchase_revenue", col("ecommerce.purchase_revenue_in_usd") / col("ecommerce.total_item_quantity"))
         .sort(col("avg_purchase_revenue").desc())
        )

display(revDF)

In [0]:
%sql
CREATE TABLE IF NOT EXISTS events USING parquet OPTIONS (path "/mnt/training/ecommerce/events/events.parquet");

In [0]:
eventsPath = "/mnt/training/ecommerce/events/events.parquet"
eventsDF = spark.read.format("parquet").load(eventsPath)

In [0]:
revDF = (eventsDF.filter(col("ecommerce.purchase_revenue_in_usd").isNotNull())
         .withColumn("purchase_revenue", (col("ecommerce.purchase_revenue_in_usd")*100).cast("int")) 
         .withColumn("average_purchase_revenue", (col("ecommerce.purchase_revenue_in_usd")/ col("ecommerce.total_item_quantity"))*100) 
         .sort(col("average_purchase_revenue").desc())
      )

## DataFrame Transformation Methods
| Method | Description |
| --- | --- |
| select | Returns a new DataFrame by computing given expression for each element |
| drop | Returns a new DataFrame with a column dropped |
| withColumnRenamed | Returns a new DataFrame with a column renamed |
| withColumn | Returns a new DataFrame by adding a column or replacing the existing column that has the same name |
| filter, where | Filters rows using the given condition |
| sort, orderBy | Returns a new DataFrame sorted by the given expressions |
| dropDuplicates, distinct | Returns a new DataFrame with duplicate rows removed |
| limit | Returns a new DataFrame by taking the first n rows |
| groupBy | Groups the DataFrame using the specified columns, so we can run aggregation on them |

### Subset columns
Use DataFrame transformations to subset columns

#### `select()`
Selects a list of columns or column based expressions

In [0]:
devicesDF = eventsDF.select("user_id", "device")
display(devicesDF)

user_id device UA000000107379500 macOS UA000000107359357 Windows UA000000107375547 macOS UA000000107370581 iOS UA000000107377108 Windows UA000000107377161 Windows UA000000107370851 iOS UA000000107360961 macOS UA000000107376205 Android UA000000107359805 Windows UA000000107369909 iOS UA000000107371743 Linux UA000000107380961 Android UA000000107377487 Linux UA000000107357350 macOS UA000000107359573 iOS UA000000107364368 macOS UA000000107357467 Windows UA000000107369512 iOS UA000000107365065 iOS UA000000107364813 Android UA000000107374663 iOS UA000000107382638 Android UA000000107367922 Windows UA000000107366779 Android UA000000107374215 Windows UA000000107380780 macOS UA000000107359571 iOS UA000000107376278 macOS UA000000107363006 macOS UA000000107360852 iOS UA000000107381241 Windows UA000000107377238 macOS UA000000107371192 Linux UA000000107367048 Windows UA000000107379637 Windows UA000000107371070 Android UA000000107378173 Windows UA000000107373270 iOS UA000000107375316 Windows UA000000107374020 Android UA000000107357480 Android UA000000107364704 Chrome OS UA000000107362707 Windows UA000000107372672 Android UA000000107375642 Chrome OS UA000000107380952 macOS UA000000107370829 macOS UA000000107361649 macOS UA000000107377392 Windows UA000000107360196 Linux UA000000107363249 macOS UA000000107372505 Windows UA000000107358569 Android UA000000107378924 Windows UA000000107380991 macOS UA000000107361989 iOS UA000000107358571 macOS UA000000107366349 Linux UA000000107370853 Android UA000000107380222 Chrome OS UA000000107368830 Android UA000000107380441 Android UA000000107370279 iOS UA000000107375824 iOS UA000000107369710 Windows UA000000107379918 Windows UA000000107361970 Android UA000000107357319 Chrome OS UA000000107359552 Windows UA000000107368410 iOS UA000000107369252 macOS UA000000107377217 Windows UA000000107382225 Android UA000000107371554 iOS UA000000107357359 macOS UA000000107361812 Chrome OS UA000000107377843 macOS UA000000107358307 Android UA000000107374194 Linux UA000000107364642 macOS UA000000107368326 macOS UA000000107360046 Windows UA000000107361826 Chrome OS UA000000107363816 iOS UA000000107370641 iOS UA000000107376495 Android UA000000107372186 Android UA000000107365658 Android UA000000107360336 iOS UA000000107371458 Android UA000000107359727 macOS UA000000107380353 Windows UA000000107362695 iOS UA000000107373722 Android UA000000107382278 iOS UA000000107381321 iOS UA000000107375378 Windows UA000000107378202 Windows UA000000107380610 macOS UA000000107358069 Windows UA000000107360551 macOS UA000000107367705 iOS UA000000107371057 Android UA000000107367938 Android UA000000107373956 Linux UA000000107367963 Android UA000000107374820 Android UA000000107375426 macOS UA000000107359991 macOS UA000000107378178 Android UA000000107378521 Android UA000000107366709 macOS UA000000107381140 Windows UA000000107375805 macOS UA000000107369237 Linux UA000000107361827 Windows UA000000107363382 macOS UA000000107382864 Android UA000000107360669 Android UA000000107358089 Android UA000000107364370 macOS UA000000107364350 macOS UA000000107371380 Windows UA000000107366547 Android UA000000107359535 Windows UA000000107379188 Android UA000000107382872 iOS UA000000107360337 Windows UA000000107376481 iOS UA000000107359755 macOS UA000000107369580 iOS UA000000107370279 iOS UA000000107359699 iOS UA000000107362550 Windows UA000000107358411 Chrome OS UA000000107369024 Chrome OS UA000000107381041 Chrome OS UA000000107362902 Linux UA000000107357951 iOS UA000000107370837 iOS UA000000107374815 Android UA000000107369177 Windows UA000000107373278 Linux UA000000107359942 Chrome OS UA000000107363555 Windows UA000000107374406 Linux UA000000107369171 macOS UA000000107372452 Windows UA000000107368898 iOS UA000000107373534 Android UA000000107376770 Linux UA000000107358016 Android UA000000107361415 iOS UA000000107371892 macOS UA000000107371237 Windows UA000000107379685 macOS UA000000107371220 Android UA000000107361395 macOS UA000000107378018 iOS UA000000107362908 Android U

In [0]:
from pyspark.sql.functions import col

locationsDF = eventsDF.select(
    "user_id", 
    col("geo.city").alias("city"), 
    col("geo.state").alias("state")
)
display(locationsDF)

user_id city state UA000000107379500 Montrose MI UA000000107359357 Northampton MA UA000000107375547 Salinas CA UA000000107370581 Everett MA UA000000107377108 Cottage Grove MN UA000000107377161 Medina MN UA000000107370851 Mount Pleasant UT UA000000107360961 Piedmont AL UA000000107376205 Rancho Santa Margarita CA UA000000107359805 Elyria OH UA000000107369909 Longview WA UA000000107371743 Lyndhurst OH UA000000107380961 Jackson MO UA000000107377487 Cedar Rapids IA UA000000107357350 Phoenix AZ UA000000107359573 Warwick RI UA000000107364368 Everett WA UA000000107357467 Concord CA UA000000107369512 Dunwoody GA UA000000107365065 Rochester MN UA000000107364813 Raleigh NC UA000000107374663 Los Angeles CA UA000000107382638 New York NY UA000000107367922 Chicago IL UA000000107366779 Fayetteville AR UA000000107374215 Topeka KS UA000000107380780 Newark CA UA000000107359571 Battle Creek MI UA000000107376278 El Paso TX UA000000107363006 Sandy Springs GA UA000000107360852 Greeley CO UA000000107381241 Richland WA UA000000107377238 Camden SC UA000000107371192 Fairfield CA UA000000107367048 Jacksonville NC UA000000107379637 San Angelo TX UA000000107371070 North Canton OH UA000000107378173 Salem MA UA000000107373270 Bloomington MN UA000000107375316 Grinnell IA UA000000107374020 Philadelphia PA UA000000107357480 Richmond KY UA000000107364704 Cloquet MN UA000000107362707 Albany NY UA000000107372672 Portland OR UA000000107375642 Naperville IL UA000000107380952 Dallas TX UA000000107370829 Moreno Valley CA UA000000107361649 Dallas TX UA000000107377392 Milledgeville GA UA000000107360196 Seattle WA UA000000107363249 Norwalk CT UA000000107372505 Lynwood CA UA000000107358569 San Diego CA UA000000107378924 New York NY UA000000107380991 Davis CA UA000000107361989 Fresno CA UA000000107358571 Palmyra MO UA000000107366349 Fitchburg MA UA000000107370853 Chicago IL UA000000107380222 Bridgeton NJ UA000000107368830 Benicia CA UA000000107380441 Lake Forest CA UA000000107370279 Hollywood FL UA000000107375824 Laurens SC UA000000107369710 Bridgeton NJ UA000000107379918 Los Angeles CA UA000000107361970 Hinesville GA UA000000107357319 Egg Harbor City NJ UA000000107359552 Loveland CO UA000000107368410 Bellevue WA UA000000107369252 Sun Prairie WI UA000000107377217 Las Vegas NV UA000000107382225 Jacksonville FL UA000000107371554 Phoenix AZ UA000000107357359 Philadelphia PA UA000000107361812 San Francisco CA UA000000107377843 Spokane WA UA000000107358307 Rochester NY UA000000107374194 Round Rock TX UA000000107364642 El Monte CA UA000000107368326 Aurora CO UA000000107360046 Brownsville TX UA000000107361826 Phoenix AZ UA000000107363816 Riverton UT UA000000107370641 Santa Monica CA UA000000107376495 Plymouth MN UA000000107372186 Waupun WI UA000000107365658 Waukegan IL UA000000107360336 Old Town ME UA000000107371458 Washington DC UA000000107359727 St. Marys PA UA000000107380353 New York NY UA000000107362695 Orem UT UA000000107373722 Chicago IL UA000000107382278 Miami FL UA000000107381321 Bottineau ND UA000000107375378 Weymouth Town MA UA000000107378202 Berkeley CA UA000000107380610 Walled Lake MI UA000000107358069 Los Angeles CA UA000000107360551 Philadelphia PA UA000000107367705 Phoenix AZ UA000000107371057 King City CA UA000000107367938 Piqua OH UA000000107373956 San Jose CA UA000000107367963 Delray Beach FL UA000000107374820 Oakland CA UA000000107375426 New York NY UA000000107359991 Jersey City NJ UA000000107378178 Murphy TX UA000000107378521 Calumet City IL UA000000107366709 Bellevue WA UA000000107381140 Riverside CA UA000000107375805 Los Angeles CA UA000000107369237 Brookhaven GA UA000000107361827 Los Angeles CA UA000000107363382 Reading PA UA000000107382864 New York NY UA000000107360669 California City CA UA000000107358089 Long Beach CA UA000000107364370 Wentzville MO UA000000107364350 Lincoln NE UA000000107371380 Los Angeles CA UA000000107366547 Frisco TX UA000000107359535 New York NY UA000000107379188 Maple Grove MN UA000000107382872 Westland MI UA000000107360337 Cape Cor

#### `selectExpr()`
Selects a list of SQL expressions

In [0]:
appleDF = eventsDF.selectExpr("user_id", "device in ('macOS', 'iOS') as apple_user")
display(appleDF)

user_id apple_user UA000000107379500 true UA000000107359357 false UA000000107375547 true UA000000107370581 true UA000000107377108 false UA000000107377161 false UA000000107370851 true UA000000107360961 true UA000000107376205 false UA000000107359805 false UA000000107369909 true UA000000107371743 false UA000000107380961 false UA000000107377487 false UA000000107357350 true UA000000107359573 true UA000000107364368 true UA000000107357467 false UA000000107369512 true UA000000107365065 true UA000000107364813 false UA000000107374663 true UA000000107382638 false UA000000107367922 false UA000000107366779 false UA000000107374215 false UA000000107380780 true UA000000107359571 true UA000000107376278 true UA000000107363006 true UA000000107360852 true UA000000107381241 false UA000000107377238 true UA000000107371192 false UA000000107367048 false UA000000107379637 false UA000000107371070 false UA000000107378173 false UA000000107373270 true UA000000107375316 false UA000000107374020 false UA000000107357480 false UA000000107364704 false UA000000107362707 false UA000000107372672 false UA000000107375642 false UA000000107380952 true UA000000107370829 true UA000000107361649 true UA000000107377392 false UA000000107360196 false UA000000107363249 true UA000000107372505 false UA000000107358569 false UA000000107378924 false UA000000107380991 true UA000000107361989 true UA000000107358571 true UA000000107366349 false UA000000107370853 false UA000000107380222 false UA000000107368830 false UA000000107380441 false UA000000107370279 true UA000000107375824 true UA000000107369710 false UA000000107379918 false UA000000107361970 false UA000000107357319 false UA000000107359552 false UA000000107368410 true UA000000107369252 true UA000000107377217 false UA000000107382225 false UA000000107371554 true UA000000107357359 true UA000000107361812 false UA000000107377843 true UA000000107358307 false UA000000107374194 false UA000000107364642 true UA000000107368326 true UA000000107360046 false UA000000107361826 false UA000000107363816 true UA000000107370641 true UA000000107376495 false UA000000107372186 false UA000000107365658 false UA000000107360336 true UA000000107371458 false UA000000107359727 true UA000000107380353 false UA000000107362695 true UA000000107373722 false UA000000107382278 true UA000000107381321 true UA000000107375378 false UA000000107378202 false UA000000107380610 true UA000000107358069 false UA000000107360551 true UA000000107367705 true UA000000107371057 false UA000000107367938 false UA000000107373956 false UA000000107367963 false UA000000107374820 false UA000000107375426 true UA000000107359991 true UA000000107378178 false UA000000107378521 false UA000000107366709 true UA000000107381140 false UA000000107375805 true UA000000107369237 false UA000000107361827 false UA000000107363382 true UA000000107382864 false UA000000107360669 false UA000000107358089 false UA000000107364370 true UA000000107364350 true UA000000107371380 false UA000000107366547 false UA000000107359535 false UA000000107379188 false UA000000107382872 true UA000000107360337 false UA000000107376481 true UA000000107359755 true UA000000107369580 true UA000000107370279 true UA000000107359699 true UA000000107362550 false UA000000107358411 false UA000000107369024 false UA000000107381041 false UA000000107362902 false UA000000107357951 true UA000000107370837 true UA000000107374815 false UA000000107369177 false UA000000107373278 false UA000000107359942 false UA000000107363555 false UA000000107374406 false UA000000107369171 true UA000000107372452 false UA000000107368898 true UA000000107373534 false UA000000107376770 false UA000000107358016 false UA000000107361415 true UA000000107371892 true UA000000107371237 false UA000000107379685 true UA000000107371220 false UA000000107361395 true UA000000107378018 true UA000000107362908 false UA000000107363749 false UA000000107358073 false UA000000107380379 true UA000000107376638 false UA000000107367064 false UA000000107358756 false UA000000107364431 true UA000000107364843 

#### `drop()`
Returns a new DataFrame after dropping the given column, specified as a string or Column object

Use strings to specify multiple columns

In [0]:
anonymousDF = eventsDF.drop("user_id", "geo", "device")
display(anonymousDF)

ecommerce event_name event_previous_timestamp event_timestamp items traffic_source user_first_touch_timestamp List(null, null, null) warranty 1593878899217692 1593878946592107 List() google 1593878899217692 List(null, null, null) press 1593876662175340 1593877011756535 List() google 1593876662175340 List(null, null, null) add_item 1593878792892652 1593878815459100 List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) youtube 1593878455472030 List(null, null, null) mattresses 1593878178791663 1593878809276923 List() facebook 1593877903116176 List(null, null, null) mattresses null 1593878628143633 List() google 1593878628143633 List(null, null, null) main null 1593878634344194 List() youtube 1593878634344194 List(null, null, null) main null 1593877936171803 List() direct 1593877936171803 List(null, null, null) main null 1593876843215329 List() instagram 1593876843215329 List(null, null, null) warranty 1593878529774474 1593879213196400 List() instagram 1593878529774474 List(null, null, null) main null 1593876713246514 List() facebook 1593876713246514 List(null, null, null) original 1593878068949001 1593878170903989 List() google 1593877826716812 List(null, null, null) main null 1593878036347579 List() direct 1593878036347579 List(null, null, null) down 1593879057792999 1593879125815755 List() facebook 1593879057792999 List(null, null, null) main null 1593878672173087 List() google 1593878672173087 List(null, null, null) main null 1593876429415452 List() google 1593876429415452 List(null, null, null) mattresses null 1593876687337581 List() google 1593876687337581 List(null, null, null) premium 1593877223736871 1593877973962436 List() instagram 1593877223736871 List(null, null, null) reviews 1593876442432487 1593876944661570 List() direct 1593876442432487 List(null, null, null) original 1593877781854634 1593877788141768 List() google 1593877781854634 List(null, null, null) main 1593877445670953 1593877497207417 List() facebook 1593877300577217 List(null, null, null) main null 1593877271099453 List() direct 1593877271099453 List(null, null, null) reviews 1593878353149193 1593878356880855 List() facebook 1593878353149193 List(null, null, null) main null 1593879239050626 List() direct 1593879239050626 List(null, null, null) mattresses null 1593877608354608 List() google 1593877608354608 List(null, null, null) cart 1593878887634182 1593878899159806 List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) google 1593877484784180 List(null, null, null) cart 1593878838199623 1593879003979444 List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) direct 1593878302525160 List(null, null, null) main null 1593879039209043 List() direct 1593879039209043 List(null, null, null) main null 1593876687186216 List() facebook 1593876687186216 List(null, null, null) faq 1593878537597094 1593878984168461 List() direct 1593878537597094 List(null, null, null) mattresses null 1593877076686136 List() facebook 1593877076686136 List(null, null, null) main null 1593876831949693 List() google 1593876831949693 List(null, null, null) pillows null 1593879086932085 List() instagram 1593879086932085 List(null, null, null) main null 1593878642524459 List() facebook 1593878642524459 List(null, null, null) main null 1593877977050669 List() instagram 1593877977050669 List(null, null, null) pillows null 1593877512951677 List() direct 1593877512951677 List(null, null, null) mattresses null 1593878914256162 List() google 1593878914256162 List(null, null, null) warranty 1593877962951723 1593878620744974 List() instagram 1593877962951723 List(null, null, null) pillows null 1593878751138630 List() google 1593878751138630 List(null, null, null) foam 1593878204104266 1593878206468778 List() direct 1593878204104266 List(null, null, null) main null 1593878429326706 List() google 1593878429326706 List(null, null, null) checkout 1593879068779767 1593879230950221 List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) facebook 159

In [0]:
noSalesDF = eventsDF.drop(col("ecommerce"))
display(noSalesDF)

device event_name event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id macOS warranty 1593878899217692 1593878946592107 List(Montrose, MI) List() google 1593878899217692 UA000000107379500 Windows press 1593876662175340 1593877011756535 List(Northampton, MA) List() google 1593876662175340 UA000000107359357 macOS add_item 1593878792892652 1593878815459100 List(Salinas, CA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) youtube 1593878455472030 UA000000107375547 iOS mattresses 1593878178791663 1593878809276923 List(Everett, MA) List() facebook 1593877903116176 UA000000107370581 Windows mattresses null 1593878628143633 List(Cottage Grove, MN) List() google 1593878628143633 UA000000107377108 Windows main null 1593878634344194 List(Medina, MN) List() youtube 1593878634344194 UA000000107377161 iOS main null 1593877936171803 List(Mount Pleasant, UT) List() direct 1593877936171803 UA000000107370851 macOS main null 1593876843215329 List(Piedmont, AL) List() instagram 1593876843215329 UA000000107360961 Android warranty 1593878529774474 1593879213196400 List(Rancho Santa Margarita, CA) List() instagram 1593878529774474 UA000000107376205 Windows main null 1593876713246514 List(Elyria, OH) List() facebook 1593876713246514 UA000000107359805 iOS original 1593878068949001 1593878170903989 List(Longview, WA) List() google 1593877826716812 UA000000107369909 Linux main null 1593878036347579 List(Lyndhurst, OH) List() direct 1593878036347579 UA000000107371743 Android down 1593879057792999 1593879125815755 List(Jackson, MO) List() facebook 1593879057792999 UA000000107380961 Linux main null 1593878672173087 List(Cedar Rapids, IA) List() google 1593878672173087 UA000000107377487 macOS main null 1593876429415452 List(Phoenix, AZ) List() google 1593876429415452 UA000000107357350 iOS mattresses null 1593876687337581 List(Warwick, RI) List() google 1593876687337581 UA000000107359573 macOS premium 1593877223736871 1593877973962436 List(Everett, WA) List() instagram 1593877223736871 UA000000107364368 Windows reviews 1593876442432487 1593876944661570 List(Concord, CA) List() direct 1593876442432487 UA000000107357467 iOS original 1593877781854634 1593877788141768 List(Dunwoody, GA) List() google 1593877781854634 UA000000107369512 iOS main 1593877445670953 1593877497207417 List(Rochester, MN) List() facebook 1593877300577217 UA000000107365065 Android main null 1593877271099453 List(Raleigh, NC) List() direct 1593877271099453 UA000000107364813 iOS reviews 1593878353149193 1593878356880855 List(Los Angeles, CA) List() facebook 1593878353149193 UA000000107374663 Android main null 1593879239050626 List(New York, NY) List() direct 1593879239050626 UA000000107382638 Windows mattresses null 1593877608354608 List(Chicago, IL) List() google 1593877608354608 UA000000107367922 Android cart 1593878887634182 1593878899159806 List(Fayetteville, AR) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) google 1593877484784180 UA000000107366779 Windows cart 1593878838199623 1593879003979444 List(Topeka, KS) List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) direct 1593878302525160 UA000000107374215 macOS main null 1593879039209043 List(Newark, CA) List() direct 1593879039209043 UA000000107380780 iOS main null 1593876687186216 List(Battle Creek, MI) List() facebook 1593876687186216 UA000000107359571 macOS faq 1593878537597094 1593878984168461 List(El Paso, TX) List() direct 1593878537597094 UA000000107376278 macOS mattresses null 1593877076686136 List(Sandy Springs, GA) List() facebook 1593877076686136 UA000000107363006 iOS main null 1593876831949693 List(Greeley, CO) List() google 1593876831949693 UA000000107360852 Windows pillows null 1593879086932085 List(Richland, WA) List() instagram 1593879086932085 UA000000107381241 macOS main null 1593878642524459 List(Camden, SC) List() facebook 1593878642524459 UA000000107377238 Linux main null 1593877977050669 List(Fairfield, CA) Li

### Add or replace columns
Use DataFrame transformations to add or replace columns

#### `withColumn()`
Returns a new DataFrame by adding a column or replacing an existing column that has the same name.

In [0]:
mobileDF = eventsDF.withColumn("mobile", col("device").isin("iOS", "Android"))
display(mobileDF)

device ecommerce event_name event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id mobile macOS List(null, null, null) warranty 1593878899217692 1593878946592107 List(Montrose, MI) List() google 1593878899217692 UA000000107379500 false Windows List(null, null, null) press 1593876662175340 1593877011756535 List(Northampton, MA) List() google 1593876662175340 UA000000107359357 false macOS List(null, null, null) add_item 1593878792892652 1593878815459100 List(Salinas, CA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) youtube 1593878455472030 UA000000107375547 false iOS List(null, null, null) mattresses 1593878178791663 1593878809276923 List(Everett, MA) List() facebook 1593877903116176 UA000000107370581 true Windows List(null, null, null) mattresses null 1593878628143633 List(Cottage Grove, MN) List() google 1593878628143633 UA000000107377108 false Windows List(null, null, null) main null 1593878634344194 List(Medina, MN) List() youtube 1593878634344194 UA000000107377161 false iOS List(null, null, null) main null 1593877936171803 List(Mount Pleasant, UT) List() direct 1593877936171803 UA000000107370851 true macOS List(null, null, null) main null 1593876843215329 List(Piedmont, AL) List() instagram 1593876843215329 UA000000107360961 false Android List(null, null, null) warranty 1593878529774474 1593879213196400 List(Rancho Santa Margarita, CA) List() instagram 1593878529774474 UA000000107376205 true Windows List(null, null, null) main null 1593876713246514 List(Elyria, OH) List() facebook 1593876713246514 UA000000107359805 false iOS List(null, null, null) original 1593878068949001 1593878170903989 List(Longview, WA) List() google 1593877826716812 UA000000107369909 true Linux List(null, null, null) main null 1593878036347579 List(Lyndhurst, OH) List() direct 1593878036347579 UA000000107371743 false Android List(null, null, null) down 1593879057792999 1593879125815755 List(Jackson, MO) List() facebook 1593879057792999 UA000000107380961 true Linux List(null, null, null) main null 1593878672173087 List(Cedar Rapids, IA) List() google 1593878672173087 UA000000107377487 false macOS List(null, null, null) main null 1593876429415452 List(Phoenix, AZ) List() google 1593876429415452 UA000000107357350 false iOS List(null, null, null) mattresses null 1593876687337581 List(Warwick, RI) List() google 1593876687337581 UA000000107359573 true macOS List(null, null, null) premium 1593877223736871 1593877973962436 List(Everett, WA) List() instagram 1593877223736871 UA000000107364368 false Windows List(null, null, null) reviews 1593876442432487 1593876944661570 List(Concord, CA) List() direct 1593876442432487 UA000000107357467 false iOS List(null, null, null) original 1593877781854634 1593877788141768 List(Dunwoody, GA) List() google 1593877781854634 UA000000107369512 true iOS List(null, null, null) main 1593877445670953 1593877497207417 List(Rochester, MN) List() facebook 1593877300577217 UA000000107365065 true Android List(null, null, null) main null 1593877271099453 List(Raleigh, NC) List() direct 1593877271099453 UA000000107364813 true iOS List(null, null, null) reviews 1593878353149193 1593878356880855 List(Los Angeles, CA) List() facebook 1593878353149193 UA000000107374663 true Android List(null, null, null) main null 1593879239050626 List(New York, NY) List() direct 1593879239050626 UA000000107382638 true Windows List(null, null, null) mattresses null 1593877608354608 List(Chicago, IL) List() google 1593877608354608 UA000000107367922 false Android List(null, null, null) cart 1593878887634182 1593878899159806 List(Fayetteville, AR) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) google 1593877484784180 UA000000107366779 true Windows List(null, null, null) cart 1593878838199623 1593879003979444 List(Topeka, KS) List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) direct 1593878302525160 UA000000107374215 false macOS List(null, null, null) main

In [0]:
display(eventsDF.withColumn("Cities", col("geo.city").isin("Everett", "Montrose", "Salinas"))
                .filter("Cities == True"))

device ecommerce event_name event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id Cities macOS List(null, null, null) warranty 1593878899217692 1593878946592107 List(Montrose, MI) List() google 1593878899217692 UA000000107379500 true macOS List(null, null, null) add_item 1593878792892652 1593878815459100 List(Salinas, CA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) youtube 1593878455472030 UA000000107375547 true iOS List(null, null, null) mattresses 1593878178791663 1593878809276923 List(Everett, MA) List() facebook 1593877903116176 UA000000107370581 true macOS List(null, null, null) premium 1593877223736871 1593877973962436 List(Everett, WA) List() instagram 1593877223736871 UA000000107364368 true Linux List(null, null, null) add_item 1593876752928952 1593876781634367 List(Salinas, CA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) facebook 1593876752928952 UA000000107360110 true Chrome OS List(null, null, null) pillows 1593878452222535 1593878532244478 List(Salinas, CA) List() google 1593877167160537 UA000000107363819 true Windows List(null, null, null) pillows null 1593877490080721 List(Salinas, CA) List() facebook 1593877490080721 UA000000107366824 true macOS List(null, null, null) cart 1593877578341409 1593877602752023 List(Salinas, CA) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) facebook 1593877576180278 UA000000107367639 true Windows List(null, null, null) mattresses null 1593877497837665 List(Montrose, CO) List() direct 1593877497837665 UA000000107366908 true Windows List(null, null, null) delivery 1593876601379674 1593876827618536 List(Everett, WA) List() google 1593876601379674 UA000000107358843 true macOS List(null, null, null) add_item 1593877576180278 1593877578341409 List(Salinas, CA) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) facebook 1593877576180278 UA000000107367639 true Windows List(null, null, null) main 1593876827618536 1593877366973769 List(Everett, WA) List() google 1593876601379674 UA000000107358843 true iOS List(null, null, null) main null 1593878700430008 List(Everett, MA) List() google 1593878700430008 UA000000107377732 true iOS List(null, null, null) checkout 1593877382117394 1593877505941501 List(Everett, WA) List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) google 1593876876615898 UA000000107361237 true Android List(null, null, null) main null 1593878902503232 List(Salinas, CA) List() direct 1593878902503232 UA000000107379530 true macOS List(null, null, null) foam 1593878455472030 1593878552992258 List(Salinas, CA) List() youtube 1593878455472030 UA000000107375547 true Chrome OS List(null, null, null) warranty 1593431321782534 1593432233676559 List(Montrose, CO) List() email 1593431321782534 UA000000106004078 true Android List(null, null, null) main null 1593425777838959 List(Everett, WA) List() facebook 1593425777838959 UA000000105992466 true iOS List(null, null, null) pillows 1593435326398503 1593435385072079 List(Everett, WA) List(List(NEWBED10, M_STAN_T, Standard Twin Mattress, 535.5, 595.0, 1)) youtube 1593431614042641 UA000000106004849 true Linux List(null, null, null) email_coupon 1593386720140237 1593388411577180 List(Salinas, CA) List() direct 1593386637904995 UA000000105964807 true Android List(null, null, null) main null 1593436233906193 List(Everett, MA) List() google 1593436233906193 UA000000106019923 true Windows List(null, null, null) checkout 1593437092956351 1593437280233775 List(Salinas, CA) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593435151516371 UA000000106015950 true Linux List(null, null, null) main null 1593435490114805 List(Salinas, CA) List() facebook 1593435490114805 UA000000106017158 true iOS List(null, null, null) email_coupon 1593443768536126 1593443784727173 List(Salinas, CA) List() facebook 1593443768536126 UA000000106054966 true macOS List(null, null, null) mattresses 

In [0]:
display(eventsDF.filter(col("ecommerce.unique_items").isNotNull())
         .withColumn("average_purchase_revenue", ((col("ecommerce.purchase_revenue_in_usd")/col("ecommerce.total_item_quantity"))*100).cast("int"))
         .withColumn("state", col("geo.state").isin("CA"))
         .filter("state==True")
         .orderBy(col("average_purchase_revenue").desc())
        )

device ecommerce event_name event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id average_purchase_revenue state Windows List(1995.0, 1, 1) finalize 1593877957860351 1593878245298003 List(Rancho Santa Margarita, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) google 1593877273555818 UA000000107364837 199500 true Android List(1995.0, 1, 1) finalize 1593608158091859 1593610655395923 List(Orange, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) youtube 1593604357392277 UA000000106485303 199500 true macOS List(1995.0, 1, 1) finalize 1593439551062805 1593439617933160 List(Los Angeles, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) facebook 1593438829421906 UA000000106030732 199500 true macOS List(1995.0, 1, 1) finalize 1593164915457780 1593164958009379 List(South El Monte, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) google 1593163464873878 UA000000105187571 199500 true Linux List(1995.0, 1, 1) finalize 1593604474704238 1593604512139307 List(Daly City, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) google 1593600130952042 UA000000106474698 199500 true macOS List(1995.0, 1, 1) finalize 1593186873252444 1593187155737576 List(Foster City, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) google 1593181504189185 UA000000105243151 199500 true iOS List(1995.0, 1, 1) finalize 1593447348154121 1593447865950398 List(Cupertino, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) google 1593442146181947 UA000000106046395 199500 true Windows List(1995.0, 1, 1) finalize 1593182323731571 1593182341549092 List(Huntington Beach, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) facebook 1593178009281894 UA000000105226459 199500 true Chrome OS List(1995.0, 1, 1) finalize 1593266709663555 1593267001502519 List(Perris, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) instagram 1593263431371710 UA000000105464467 199500 true macOS List(1995.0, 1, 1) finalize 1592763824575449 1592764122740370 List(Sunnyvale, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) instagram 1592757832733826 UA000000104076430 199500 true Chrome OS List(1995.0, 1, 1) finalize 1593444104715318 1593444615767034 List(Merced, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) google 1593442668255503 UA000000106049042 199500 true Android List(1995.0, 1, 1) finalize 1592582846445328 1592583882540871 List(San Jose, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) facebook 1592578616767704 UA000000103401158 199500 true Linux List(1995.0, 1, 1) finalize 1593612652482771 1593612928323940 List(Los Angeles, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) instagram 1593607695791679 UA000000106496489 199500 true macOS List(1995.0, 1, 1) finalize 1592584815637202 1592585024116593 List(Temple City, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) google 1592580563917828 UA000000103414013 199500 true iOS List(1995.0, 1, 1) finalize 1593396384083101 1593396399133032 List(Fresno, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) google 1593391488692086 UA000000105973128 199500 true macOS List(1995.0, 1, 1) finalize 1592574645043712 1592574672178901 List(Oakland, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) instagram 1592572558549718 UA000000103366485 199500 true Android List(1995.0, 1, 1) finalize 1592659908495005 1592662497424208 List(Santa Monica, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) youtube 1592658971543315 UA000000103655715 199500 true Linux List(1995.0, 1, 1) finalize 1592739793356264 1592740040517003 List(San Diego, CA) List(List(null, M_PREM_K, Premium King Mattress, 1995.0, 1995.0, 1)) instagram 1592736979561759 UA000000103955

In [0]:
purchaseQuantityDF = eventsDF.withColumn("purchase_quantity", col("ecommerce.total_item_quantity").cast("int"))
purchaseQuantityDF.printSchema()

root
 |-- device: string (nullable = true)
 |-- ecommerce: struct (nullable = true)
 |    |-- purchase_revenue_in_usd: double (nullable = true)
 |    |-- total_item_quantity: long (nullable = true)
 |    |-- unique_items: long (nullable = true)
 |-- event_name: string (nullable = true)
 |-- event_previous_timestamp: long (nullable = true)
 |-- event_timestamp: long (nullable = true)
 |-- geo: struct (nullable = true)
 |    |-- city: string (nullable = true)
 |    |-- state: string (nullable = true)
 |-- items: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- coupon: string (nullable = true)
 |    |    |-- item_id: string (nullable = true)
 |    |    |-- item_name: string (nullable = true)
 |    |    |-- item_revenue_in_usd: double (nullable = true)
 |    |    |-- price_in_usd: double (nullable = true)
 |    |    |-- quantity: long (nullable = true)
 |-- traffic_source: string (nullable = true)
 |-- user_first_touch_timestamp: long (nullable = true)

#### `withColumnRenamed()`
Returns a new DataFrame with a column renamed.

In [0]:
locationDF = eventsDF.withColumnRenamed("geo", "location")
display(locationDF)

device ecommerce event_name event_previous_timestamp event_timestamp location items traffic_source user_first_touch_timestamp user_id macOS List(null, null, null) warranty 1593878899217692 1593878946592107 List(Montrose, MI) List() google 1593878899217692 UA000000107379500 Windows List(null, null, null) press 1593876662175340 1593877011756535 List(Northampton, MA) List() google 1593876662175340 UA000000107359357 macOS List(null, null, null) add_item 1593878792892652 1593878815459100 List(Salinas, CA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) youtube 1593878455472030 UA000000107375547 iOS List(null, null, null) mattresses 1593878178791663 1593878809276923 List(Everett, MA) List() facebook 1593877903116176 UA000000107370581 Windows List(null, null, null) mattresses null 1593878628143633 List(Cottage Grove, MN) List() google 1593878628143633 UA000000107377108 Windows List(null, null, null) main null 1593878634344194 List(Medina, MN) List() youtube 1593878634344194 UA000000107377161 iOS List(null, null, null) main null 1593877936171803 List(Mount Pleasant, UT) List() direct 1593877936171803 UA000000107370851 macOS List(null, null, null) main null 1593876843215329 List(Piedmont, AL) List() instagram 1593876843215329 UA000000107360961 Android List(null, null, null) warranty 1593878529774474 1593879213196400 List(Rancho Santa Margarita, CA) List() instagram 1593878529774474 UA000000107376205 Windows List(null, null, null) main null 1593876713246514 List(Elyria, OH) List() facebook 1593876713246514 UA000000107359805 iOS List(null, null, null) original 1593878068949001 1593878170903989 List(Longview, WA) List() google 1593877826716812 UA000000107369909 Linux List(null, null, null) main null 1593878036347579 List(Lyndhurst, OH) List() direct 1593878036347579 UA000000107371743 Android List(null, null, null) down 1593879057792999 1593879125815755 List(Jackson, MO) List() facebook 1593879057792999 UA000000107380961 Linux List(null, null, null) main null 1593878672173087 List(Cedar Rapids, IA) List() google 1593878672173087 UA000000107377487 macOS List(null, null, null) main null 1593876429415452 List(Phoenix, AZ) List() google 1593876429415452 UA000000107357350 iOS List(null, null, null) mattresses null 1593876687337581 List(Warwick, RI) List() google 1593876687337581 UA000000107359573 macOS List(null, null, null) premium 1593877223736871 1593877973962436 List(Everett, WA) List() instagram 1593877223736871 UA000000107364368 Windows List(null, null, null) reviews 1593876442432487 1593876944661570 List(Concord, CA) List() direct 1593876442432487 UA000000107357467 iOS List(null, null, null) original 1593877781854634 1593877788141768 List(Dunwoody, GA) List() google 1593877781854634 UA000000107369512 iOS List(null, null, null) main 1593877445670953 1593877497207417 List(Rochester, MN) List() facebook 1593877300577217 UA000000107365065 Android List(null, null, null) main null 1593877271099453 List(Raleigh, NC) List() direct 1593877271099453 UA000000107364813 iOS List(null, null, null) reviews 1593878353149193 1593878356880855 List(Los Angeles, CA) List() facebook 1593878353149193 UA000000107374663 Android List(null, null, null) main null 1593879239050626 List(New York, NY) List() direct 1593879239050626 UA000000107382638 Windows List(null, null, null) mattresses null 1593877608354608 List(Chicago, IL) List() google 1593877608354608 UA000000107367922 Android List(null, null, null) cart 1593878887634182 1593878899159806 List(Fayetteville, AR) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) google 1593877484784180 UA000000107366779 Windows List(null, null, null) cart 1593878838199623 1593879003979444 List(Topeka, KS) List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) direct 1593878302525160 UA000000107374215 macOS List(null, null, null) main null 1593879039209043 List(Newark, CA) List() direct 1593879039209043 UA000000107380780 iOS List(null, null, null) main null 1593876687186216 Lis

### Subset Rows
Use DataFrame transformations to subset rows

#### `filter()`
Filters rows using the given SQL expression or column based condition.

In [0]:
purchasesDF = eventsDF.filter("ecommerce.total_item_quantity > 0")
display(purchasesDF)

In [0]:
revenueDF = eventsDF.filter(col("ecommerce.purchase_revenue_in_usd").isNotNull())
display(revenueDF)

In [0]:
androidDF = eventsDF.filter((col("traffic_source") != "direct") & (col("device") == "Android"))
display(androidDF)

#### `dropDuplicates()`
Returns a new DataFrame with duplicate rows removed, optionally considering only a subset of columns.

##### Alias: `distinct`

In [0]:
eventsDF.distinct()

In [0]:
distinctUsersDF = eventsDF.dropDuplicates(["user_id"])
display(distinctUsersDF)

#### `limit()`
Returns a new DataFrame by taking the first n rows.

In [0]:
limitDF = eventsDF.limit(100)
display(limitDF)

### Sort rows
Use DataFrame transformations to sort rows

#### `sort()`
Returns a new DataFrame sorted by the given columns or expressions.

##### Alias: `orderBy`

In [0]:
increaseTimestampsDF = eventsDF.sort("event_timestamp")
display(increaseTimestampsDF)

In [0]:
decreaseTimestampsDF = eventsDF.sort(col("event_timestamp").desc())
display(decreaseTimestampsDF)

In [0]:
increaseSessionsDF = eventsDF.orderBy(["user_first_touch_timestamp", "event_timestamp"])
display(increaseSessionsDF)

In [0]:
decreaseSessionsDF = eventsDF.sort(col("user_first_touch_timestamp").desc(), col("event_timestamp"))
display(decreaseSessionsDF)

# Purchase Revenues Lab

Prepare dataset of events with purchase revenue.

##### Tasks
1. Extract purchase revenue for each event
2. Filter events where revenue is not null
3. Check what types of events have revenue
4. Drop unneeded column

##### Methods
- DataFrame: `select`, `drop`, `withColumn`, `filter`, `dropDuplicates`
- Column: `isNotNull`

In [0]:
eventsDF = spark.read.parquet(eventsPath)
display(eventsDF)

device ecommerce event_name event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id macOS List(null, null, null) warranty 1593878899217692 1593878946592107 List(Montrose, MI) List() google 1593878899217692 UA000000107379500 Windows List(null, null, null) press 1593876662175340 1593877011756535 List(Northampton, MA) List() google 1593876662175340 UA000000107359357 macOS List(null, null, null) add_item 1593878792892652 1593878815459100 List(Salinas, CA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) youtube 1593878455472030 UA000000107375547 iOS List(null, null, null) mattresses 1593878178791663 1593878809276923 List(Everett, MA) List() facebook 1593877903116176 UA000000107370581 Windows List(null, null, null) mattresses null 1593878628143633 List(Cottage Grove, MN) List() google 1593878628143633 UA000000107377108 Windows List(null, null, null) main null 1593878634344194 List(Medina, MN) List() youtube 1593878634344194 UA000000107377161 iOS List(null, null, null) main null 1593877936171803 List(Mount Pleasant, UT) List() direct 1593877936171803 UA000000107370851 macOS List(null, null, null) main null 1593876843215329 List(Piedmont, AL) List() instagram 1593876843215329 UA000000107360961 Android List(null, null, null) warranty 1593878529774474 1593879213196400 List(Rancho Santa Margarita, CA) List() instagram 1593878529774474 UA000000107376205 Windows List(null, null, null) main null 1593876713246514 List(Elyria, OH) List() facebook 1593876713246514 UA000000107359805 iOS List(null, null, null) original 1593878068949001 1593878170903989 List(Longview, WA) List() google 1593877826716812 UA000000107369909 Linux List(null, null, null) main null 1593878036347579 List(Lyndhurst, OH) List() direct 1593878036347579 UA000000107371743 Android List(null, null, null) down 1593879057792999 1593879125815755 List(Jackson, MO) List() facebook 1593879057792999 UA000000107380961 Linux List(null, null, null) main null 1593878672173087 List(Cedar Rapids, IA) List() google 1593878672173087 UA000000107377487 macOS List(null, null, null) main null 1593876429415452 List(Phoenix, AZ) List() google 1593876429415452 UA000000107357350 iOS List(null, null, null) mattresses null 1593876687337581 List(Warwick, RI) List() google 1593876687337581 UA000000107359573 macOS List(null, null, null) premium 1593877223736871 1593877973962436 List(Everett, WA) List() instagram 1593877223736871 UA000000107364368 Windows List(null, null, null) reviews 1593876442432487 1593876944661570 List(Concord, CA) List() direct 1593876442432487 UA000000107357467 iOS List(null, null, null) original 1593877781854634 1593877788141768 List(Dunwoody, GA) List() google 1593877781854634 UA000000107369512 iOS List(null, null, null) main 1593877445670953 1593877497207417 List(Rochester, MN) List() facebook 1593877300577217 UA000000107365065 Android List(null, null, null) main null 1593877271099453 List(Raleigh, NC) List() direct 1593877271099453 UA000000107364813 iOS List(null, null, null) reviews 1593878353149193 1593878356880855 List(Los Angeles, CA) List() facebook 1593878353149193 UA000000107374663 Android List(null, null, null) main null 1593879239050626 List(New York, NY) List() direct 1593879239050626 UA000000107382638 Windows List(null, null, null) mattresses null 1593877608354608 List(Chicago, IL) List() google 1593877608354608 UA000000107367922 Android List(null, null, null) cart 1593878887634182 1593878899159806 List(Fayetteville, AR) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) google 1593877484784180 UA000000107366779 Windows List(null, null, null) cart 1593878838199623 1593879003979444 List(Topeka, KS) List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) direct 1593878302525160 UA000000107374215 macOS List(null, null, null) main null 1593879039209043 List(Newark, CA) List() direct 1593879039209043 UA000000107380780 iOS List(null, null, null) main null 1593876687186216 List(Bat

### 1. Extract purchase revenue for each event
Add new column **`revenue`** by extracting **`ecommerce.purchase_revenue_in_usd`**

In [0]:
from pyspark.sql.functions import col

In [0]:
# TODO
revenueDF = eventsDF.withColumn("revenue", col("ecommerce.purchase_revenue_in_usd"))
display(revenueDF)

device ecommerce event_name event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id revenue macOS List(null, null, null) warranty 1593878899217692 1593878946592107 List(Montrose, MI) List() google 1593878899217692 UA000000107379500 null Windows List(null, null, null) press 1593876662175340 1593877011756535 List(Northampton, MA) List() google 1593876662175340 UA000000107359357 null macOS List(null, null, null) add_item 1593878792892652 1593878815459100 List(Salinas, CA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) youtube 1593878455472030 UA000000107375547 null iOS List(null, null, null) mattresses 1593878178791663 1593878809276923 List(Everett, MA) List() facebook 1593877903116176 UA000000107370581 null Windows List(null, null, null) mattresses null 1593878628143633 List(Cottage Grove, MN) List() google 1593878628143633 UA000000107377108 null Windows List(null, null, null) main null 1593878634344194 List(Medina, MN) List() youtube 1593878634344194 UA000000107377161 null iOS List(null, null, null) main null 1593877936171803 List(Mount Pleasant, UT) List() direct 1593877936171803 UA000000107370851 null macOS List(null, null, null) main null 1593876843215329 List(Piedmont, AL) List() instagram 1593876843215329 UA000000107360961 null Android List(null, null, null) warranty 1593878529774474 1593879213196400 List(Rancho Santa Margarita, CA) List() instagram 1593878529774474 UA000000107376205 null Windows List(null, null, null) main null 1593876713246514 List(Elyria, OH) List() facebook 1593876713246514 UA000000107359805 null iOS List(null, null, null) original 1593878068949001 1593878170903989 List(Longview, WA) List() google 1593877826716812 UA000000107369909 null Linux List(null, null, null) main null 1593878036347579 List(Lyndhurst, OH) List() direct 1593878036347579 UA000000107371743 null Android List(null, null, null) down 1593879057792999 1593879125815755 List(Jackson, MO) List() facebook 1593879057792999 UA000000107380961 null Linux List(null, null, null) main null 1593878672173087 List(Cedar Rapids, IA) List() google 1593878672173087 UA000000107377487 null macOS List(null, null, null) main null 1593876429415452 List(Phoenix, AZ) List() google 1593876429415452 UA000000107357350 null iOS List(null, null, null) mattresses null 1593876687337581 List(Warwick, RI) List() google 1593876687337581 UA000000107359573 null macOS List(null, null, null) premium 1593877223736871 1593877973962436 List(Everett, WA) List() instagram 1593877223736871 UA000000107364368 null Windows List(null, null, null) reviews 1593876442432487 1593876944661570 List(Concord, CA) List() direct 1593876442432487 UA000000107357467 null iOS List(null, null, null) original 1593877781854634 1593877788141768 List(Dunwoody, GA) List() google 1593877781854634 UA000000107369512 null iOS List(null, null, null) main 1593877445670953 1593877497207417 List(Rochester, MN) List() facebook 1593877300577217 UA000000107365065 null Android List(null, null, null) main null 1593877271099453 List(Raleigh, NC) List() direct 1593877271099453 UA000000107364813 null iOS List(null, null, null) reviews 1593878353149193 1593878356880855 List(Los Angeles, CA) List() facebook 1593878353149193 UA000000107374663 null Android List(null, null, null) main null 1593879239050626 List(New York, NY) List() direct 1593879239050626 UA000000107382638 null Windows List(null, null, null) mattresses null 1593877608354608 List(Chicago, IL) List() google 1593877608354608 UA000000107367922 null Android List(null, null, null) cart 1593878887634182 1593878899159806 List(Fayetteville, AR) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) google 1593877484784180 UA000000107366779 null Windows List(null, null, null) cart 1593878838199623 1593879003979444 List(Topeka, KS) List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) direct 1593878302525160 UA000000107374215 null macOS List(null, null, null) main null 1593879

**CHECK YOUR WORK**

In [0]:
expected1 = [5830.0, 5485.0, 5289.0, 5219.1, 5180.0, 5175.0, 5125.0, 5030.0, 4985.0, 4985.0]
result1 = [row.revenue for row in revenueDF.sort(col("revenue").desc_nulls_last()).limit(10).collect()]

assert(expected1 == result1)

### 2. Filter events where revenue is not null
Filter for records where **`revenue`** is not **`null`**

In [0]:
# TODO
purchasesDF = revenueDF.filter(col("revenue").isNotNull())
display(purchasesDF)

device ecommerce event_name event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id revenue Linux List(1195.0, 1, 1) finalize 1593878893766134 1593878897648871 List(Shawnee, KS) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593876996316576 UA000000107362263 1195.0 iOS List(1045.0, 1, 1) finalize 1593878485345763 1593878487460247 List(Detroit, MI) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) facebook 1593877230282722 UA000000107364432 1045.0 Android List(595.0, 1, 1) finalize 1593877930076602 1593878966392505 List(East Chicago, IN) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) google 1593876889575474 UA000000107361347 595.0 iOS List(2290.0, 2, 2) finalize 1593877650094042 1593877652106953 List(Warwick, RI) List(List(null, M_PREM_F, Premium Full Mattress, 1695.0, 1695.0, 1), List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) google 1593876687337581 UA000000107359573 2290.0 macOS List(945.0, 1, 1) finalize 1593879151529456 1593879197837168 List(Boonville, MO) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) facebook 1593878603312910 UA000000107376872 945.0 Windows List(595.0, 1, 1) finalize 1593877908876473 1593878020119079 List(Hampton, VA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) google 1593877033894464 UA000000107362622 595.0 Android List(945.0, 1, 1) finalize 1593878355764861 1593878641498265 List(White Bear Lake, MN) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) direct 1593877080764516 UA000000107363039 945.0 Chrome OS List(1095.0, 1, 1) finalize 1593879073813036 1593879191730221 List(San Antonio, TX) List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) instagram 1593877153633764 UA000000107363715 1095.0 macOS List(1045.0, 1, 1) finalize 1593877425584678 1593877429621158 List(Searcy, AR) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) direct 1593876851338276 UA000000107361027 1045.0 iOS List(1045.0, 1, 1) finalize 1593878984623390 1593879046209960 List(Southport, IN) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) instagram 1593876574686487 UA000000107358614 1045.0 Windows List(1045.0, 1, 1) finalize 1593434694145790 1593434696316863 List(Columbus, OH) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) instagram 1593432259276789 UA000000106006620 1045.0 macOS List(1640.0, 2, 2) finalize 1593436589297426 1593436628314991 List(St. Petersburg, FL) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1), List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) facebook 1593433771174842 UA000000106011218 1640.0 Chrome OS List(654.0, 2, 2) finalize 1593427561736870 1593428248499261 List(Farley, IA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1), List(null, P_FOAM_S, Standard Foam Pillow, 59.0, 59.0, 1)) google 1593424867073851 UA000000105991167 654.0 Windows List(1045.0, 1, 1) finalize 1593388148852162 1593388365815897 List(Houston, TX) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) direct 1593383873231306 UA000000105957934 1045.0 Windows List(1795.0, 1, 1) finalize 1593399598968123 1593399696924475 List(Monroe, LA) List(List(null, M_PREM_Q, Premium Queen Mattress, 1795.0, 1795.0, 1)) facebook 1593398458152390 UA000000105978828 1795.0 Android List(1195.0, 1, 1) finalize 1593416200959556 1593416273461695 List(Donaldsonville, LA) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593415794401939 UA000000105983663 1195.0 iOS List(1195.0, 1, 1) finalize 1593394478371736 1593395580886846 List(Shreveport, LA) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593388592209010 UA000000105968663 1195.0 iOS List(1128.6, 2, 2) finalize 1593763506976463 1593763527292050 List(San Ramon, CA) List(List(NEWBED10, M_STAN_K, Standard King Mattress, 10

**CHECK YOUR WORK**

In [0]:
assert purchasesDF.filter(col("revenue").isNull()).count() == 0, "Nulls in 'revenue' column"

### 3. Check what types of events have revenue
Find unique **`event_name`** values in **`purchasesDF`** in one of two ways:
- Select "event_name" and get distinct records
- Drop duplicate records based on the "event_name" only

<img src="https://files.training.databricks.com/images/icon_hint_32.png" alt="Hint"> There's only one event associated with revenues

In [0]:
# TODO
distinctDF = purchasesDF.dropDuplicates(['event_name'])
display(distinctDF)

device ecommerce event_name event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id revenue Linux List(1195.0, 1, 1) finalize 1593878893766134 1593878897648871 List(Shawnee, KS) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593876996316576 UA000000107362263 1195.0

### 4. Drop unneeded column
Since there's only one event type, drop **`event_name`** from **`purchasesDF`**.

In [0]:
# TODO
finalDF = purchasesDF.drop(col('event_name'))
display(finalDF)

device ecommerce event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id revenue Linux List(1195.0, 1, 1) 1593878893766134 1593878897648871 List(Shawnee, KS) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593876996316576 UA000000107362263 1195.0 iOS List(1045.0, 1, 1) 1593878485345763 1593878487460247 List(Detroit, MI) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) facebook 1593877230282722 UA000000107364432 1045.0 Android List(595.0, 1, 1) 1593877930076602 1593878966392505 List(East Chicago, IN) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) google 1593876889575474 UA000000107361347 595.0 iOS List(2290.0, 2, 2) 1593877650094042 1593877652106953 List(Warwick, RI) List(List(null, M_PREM_F, Premium Full Mattress, 1695.0, 1695.0, 1), List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) google 1593876687337581 UA000000107359573 2290.0 macOS List(945.0, 1, 1) 1593879151529456 1593879197837168 List(Boonville, MO) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) facebook 1593878603312910 UA000000107376872 945.0 Windows List(595.0, 1, 1) 1593877908876473 1593878020119079 List(Hampton, VA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) google 1593877033894464 UA000000107362622 595.0 Android List(945.0, 1, 1) 1593878355764861 1593878641498265 List(White Bear Lake, MN) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) direct 1593877080764516 UA000000107363039 945.0 Chrome OS List(1095.0, 1, 1) 1593879073813036 1593879191730221 List(San Antonio, TX) List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) instagram 1593877153633764 UA000000107363715 1095.0 macOS List(1045.0, 1, 1) 1593877425584678 1593877429621158 List(Searcy, AR) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) direct 1593876851338276 UA000000107361027 1045.0 iOS List(1045.0, 1, 1) 1593878984623390 1593879046209960 List(Southport, IN) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) instagram 1593876574686487 UA000000107358614 1045.0 Windows List(1045.0, 1, 1) 1593434694145790 1593434696316863 List(Columbus, OH) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) instagram 1593432259276789 UA000000106006620 1045.0 macOS List(1640.0, 2, 2) 1593436589297426 1593436628314991 List(St. Petersburg, FL) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1), List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) facebook 1593433771174842 UA000000106011218 1640.0 Chrome OS List(654.0, 2, 2) 1593427561736870 1593428248499261 List(Farley, IA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1), List(null, P_FOAM_S, Standard Foam Pillow, 59.0, 59.0, 1)) google 1593424867073851 UA000000105991167 654.0 Windows List(1045.0, 1, 1) 1593388148852162 1593388365815897 List(Houston, TX) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) direct 1593383873231306 UA000000105957934 1045.0 Windows List(1795.0, 1, 1) 1593399598968123 1593399696924475 List(Monroe, LA) List(List(null, M_PREM_Q, Premium Queen Mattress, 1795.0, 1795.0, 1)) facebook 1593398458152390 UA000000105978828 1795.0 Android List(1195.0, 1, 1) 1593416200959556 1593416273461695 List(Donaldsonville, LA) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593415794401939 UA000000105983663 1195.0 iOS List(1195.0, 1, 1) 1593394478371736 1593395580886846 List(Shreveport, LA) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593388592209010 UA000000105968663 1195.0 iOS List(1128.6, 2, 2) 1593763506976463 1593763527292050 List(San Ramon, CA) List(List(NEWBED10, M_STAN_K, Standard King Mattress, 1075.5, 1195.0, 1), List(NEWBED10, P_FOAM_S, Standard Foam Pillow, 53.1, 59.0, 1)) email 1593439553381667 UA000000106033948 1128.6 Android List(1075.5, 1, 1) 1593529030162886 

**CHECK YOUR WORK**

In [0]:
expected_columns = {"device", "ecommerce", "event_previous_timestamp", "event_timestamp",
                    "geo", "items", "revenue", "traffic_source",
                    "user_first_touch_timestamp", "user_id"}
assert(set(finalDF.columns) == expected_columns)

### 5. Chain all the steps above excluding step 3

In [0]:
# TODO
finalDF = (eventsDF
                 .filter(col("ecommerce.purchase_revenue_in_usd").isNotNull())
                 .withColumn("revenue", col("ecommerce.purchase_revenue_in_usd"))
                 .drop(col("event_name"))  
          )

display(finalDF)

device ecommerce event_previous_timestamp event_timestamp geo items traffic_source user_first_touch_timestamp user_id revenue Linux List(1195.0, 1, 1) 1593878893766134 1593878897648871 List(Shawnee, KS) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593876996316576 UA000000107362263 1195.0 iOS List(1045.0, 1, 1) 1593878485345763 1593878487460247 List(Detroit, MI) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) facebook 1593877230282722 UA000000107364432 1045.0 Android List(595.0, 1, 1) 1593877930076602 1593878966392505 List(East Chicago, IN) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) google 1593876889575474 UA000000107361347 595.0 iOS List(2290.0, 2, 2) 1593877650094042 1593877652106953 List(Warwick, RI) List(List(null, M_PREM_F, Premium Full Mattress, 1695.0, 1695.0, 1), List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) google 1593876687337581 UA000000107359573 2290.0 macOS List(945.0, 1, 1) 1593879151529456 1593879197837168 List(Boonville, MO) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) facebook 1593878603312910 UA000000107376872 945.0 Windows List(595.0, 1, 1) 1593877908876473 1593878020119079 List(Hampton, VA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1)) google 1593877033894464 UA000000107362622 595.0 Android List(945.0, 1, 1) 1593878355764861 1593878641498265 List(White Bear Lake, MN) List(List(null, M_STAN_F, Standard Full Mattress, 945.0, 945.0, 1)) direct 1593877080764516 UA000000107363039 945.0 Chrome OS List(1095.0, 1, 1) 1593879073813036 1593879191730221 List(San Antonio, TX) List(List(null, M_PREM_T, Premium Twin Mattress, 1095.0, 1095.0, 1)) instagram 1593877153633764 UA000000107363715 1095.0 macOS List(1045.0, 1, 1) 1593877425584678 1593877429621158 List(Searcy, AR) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) direct 1593876851338276 UA000000107361027 1045.0 iOS List(1045.0, 1, 1) 1593878984623390 1593879046209960 List(Southport, IN) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) instagram 1593876574686487 UA000000107358614 1045.0 Windows List(1045.0, 1, 1) 1593434694145790 1593434696316863 List(Columbus, OH) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) instagram 1593432259276789 UA000000106006620 1045.0 macOS List(1640.0, 2, 2) 1593436589297426 1593436628314991 List(St. Petersburg, FL) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1), List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) facebook 1593433771174842 UA000000106011218 1640.0 Chrome OS List(654.0, 2, 2) 1593427561736870 1593428248499261 List(Farley, IA) List(List(null, M_STAN_T, Standard Twin Mattress, 595.0, 595.0, 1), List(null, P_FOAM_S, Standard Foam Pillow, 59.0, 59.0, 1)) google 1593424867073851 UA000000105991167 654.0 Windows List(1045.0, 1, 1) 1593388148852162 1593388365815897 List(Houston, TX) List(List(null, M_STAN_Q, Standard Queen Mattress, 1045.0, 1045.0, 1)) direct 1593383873231306 UA000000105957934 1045.0 Windows List(1795.0, 1, 1) 1593399598968123 1593399696924475 List(Monroe, LA) List(List(null, M_PREM_Q, Premium Queen Mattress, 1795.0, 1795.0, 1)) facebook 1593398458152390 UA000000105978828 1795.0 Android List(1195.0, 1, 1) 1593416200959556 1593416273461695 List(Donaldsonville, LA) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593415794401939 UA000000105983663 1195.0 iOS List(1195.0, 1, 1) 1593394478371736 1593395580886846 List(Shreveport, LA) List(List(null, M_STAN_K, Standard King Mattress, 1195.0, 1195.0, 1)) google 1593388592209010 UA000000105968663 1195.0 iOS List(1128.6, 2, 2) 1593763506976463 1593763527292050 List(San Ramon, CA) List(List(NEWBED10, M_STAN_K, Standard King Mattress, 1075.5, 1195.0, 1), List(NEWBED10, P_FOAM_S, Standard Foam Pillow, 53.1, 59.0, 1)) email 1593439553381667 UA000000106033948 1128.6 Android List(1075.5, 1, 1) 1593529030162886 

**CHECK YOUR WORK**

In [0]:
assert(finalDF.count() == 180678)

In [0]:
expected_columns = {"device", "ecommerce", "event_previous_timestamp", "event_timestamp",
                    "geo", "items", "revenue", "traffic_source",
                    "user_first_touch_timestamp", "user_id"}
assert(set(finalDF.columns) == expected_columns)

### Clean up classroom

In [0]:
%run ./Includes/Classroom-Cleanup

-sandbox
&copy; 2022 Databricks, Inc. All rights reserved.<br/>
Apache, Apache Spark, Spark and the Spark logo are trademarks of the <a href="https://www.apache.org/">Apache Software Foundation</a>.<br/>
<br/>
<a href="https://databricks.com/privacy-policy">Privacy Policy</a> | <a href="https://databricks.com/terms-of-use">Terms of Use</a> | <a href="https://help.databricks.com/">Support</a>